In [1]:
import pandas as pd
import folium
from folium.plugins import MarkerCluster, Search, MiniMap
from folium import IFrame

In [2]:
data2 = pd.read_csv('blore_apartment_data.csv')
data2.head()

names             Price             Area  \
0  Salarpuria Sattva Cadenza     39 L -41.65 L        755 sq.ft   
1  Salarpuria Sattva Cadenza        55 L -75 L  1175-1275 sq.ft   
2  Salarpuria Sattva Cadenza  70.04 L -73.30 L  1335-1340 sq.ft   
3  Salarpuria Sattva Cadenza        65 L -95 L  1365-1595 sq.ft   
4              Purva Skydale  76.25 L -1.75 Cr  1273-1371 sq.ft   

            UnitType                            namesfull  
0    1 BHK Apartment  Salarpuria Sattva Cadenza bangalore  
1    2 BHK Apartment  Salarpuria Sattva Cadenza bangalore  
2  2.5 BHK Apartment  Salarpuria Sattva Cadenza bangalore  
3    3 BHK Apartment  Salarpuria Sattva Cadenza bangalore  
4    2 BHK Apartment              Purva Skydale bangalore

In [3]:
data1 = pd.read_csv('apartment_data.csv')
data1 = data1.drop(columns="geometry")
data1['combined'] = list(zip(data1.lat, data1.lon))
data1.head()

names        lat        lon  \
0               Purva Skydale bangalore  12.894033  77.662362   
1   Salarpuria Sattva Cadenza bangalore  12.889441  77.640221   
2             Shriram Summitt bangalore  12.836068  77.667242   
3               Shriram Luxor bangalore  13.085249  77.654915   
4  Ecolife Elements Of Nature bangalore  12.938728  77.731126   

                                  combined  
0           (12.894033, 77.66236169999998)  
1           (12.889441, 77.64022109999998)  
2         (12.836067800000002, 77.6672418)  
3  (13.085249000000001, 77.65491540000001)  
4          (12.9387277, 77.73112619999998)

In [122]:
max_records = 1125
BAN_COORDINATES = (12.9716, 77.5946)
map1 = folium.Map(location=BAN_COORDINATES, zoom_start=12, max_zoom = 16)
bangalore = os.path.join('bbmp.json')
map = MarkerCluster(control = False).add_to(map1)
for i in data1[0:max_records].iterrows():
    text = '<h4>' + i[1]['names'] + '</h4>'
    data3 = data2[data2.namesfull == i[1]['names']].loc[:, ['Price', 'Area', 'UnitType']]
    html = text + data3.to_html(classes="table table-striped table-hover table condensed table-responsive",index=False)
    folium.Marker(
        popup = folium.Popup(html, max_width = 400),
        location = [i[1]['lat'],i[1]['lon']] 
     ).add_to(map)
banglore_geo = folium.GeoJson(bangalore, name='bangalore',
                             tooltip= folium.features.GeoJsonTooltip(fields= ['WARD_NAME', 'WARD_NO'],
                                              aliases= ['ward name','ward no'], 
                                              labels=True, 
                                              sticky=True
                                             )).add_to(map1)
ward_search = Search(layer=banglore_geo,
                    geom_type='Polygon',
                    placeholder='Search for banglore wards',
                    collapsed=False,
                    search_label='WARD_NAME'
                    ).add_to(map1)
ward_no_search = Search(layer=banglore_geo,
                    geom_type='Polygon',
                    placeholder='Search for banglore ward_no',
                    collapsed=False,
                    search_label='WARD_NO',
                    position = 'bottomright'
                    ).add_to(map1)
minimap = MiniMap(toggle_display=True,
                  height = 200,
                  width = 200,
                  minimized = True
                 )
#t = Terminator()
#map1.add_child(t)
minimap.add_to(map1)
folium.LayerControl().add_to(map1)
display(map1)
map1.save('map.html')